# Quantum information and quantum computing - Problem set 11

### _Problem 1_ : Repetition quantum error correction code

In this notebook we will explore a simple type of error correction on quantum computers that takes advantage of repetitions. In this case, we are going to use $n=3$ physical qubits in order to represent the information contained in a single, logical qubit.

We do it by repeating the information contained in a single qubit on three qubits. Be careful that repeating does not mean "cloning". In fact, given a state

\begin{equation}
|\psi \rangle = \alpha |0\rangle + \beta |1 \rangle
\end{equation}

the repeated state is 

\begin{equation}
\alpha |000 \rangle + \beta |111 \rangle
\end{equation}

and not $|\psi \rangle \otimes |\psi \rangle \otimes |\psi \rangle$, which is in general prevented by the no-cloning theorem.

Therefore what we want to check is if the state is repeated in each of the three qubits.


In [ ]:
# First, import all the useful methods

import numpy as np
import matplotlib.pyplot as plt   
import math


from qiskit import QuantumCircuit, ClassicalRegister, QuantumRegister
from qiskit_aer import QasmSimulator

1) The first thing we want to create is a circuit that, using ancilla qubits , can spot errors by measuring the error syndromes. For $n=3$ we will need $m=2$ ancilla qubits, together with the classical registers.

In [ ]:
# Create the circuits

cq = QuantumRegister(3,'code')
aq = QuantumRegister(2,'ancilla') 
sb = ClassicalRegister(2)

qc = QuantumCircuit(cq,aq,sb)

## TO DO: write the circuit to spot errors

# Print the circuit
qc.draw('mpl', style={'name': 'iqx'})

Remember that you want a circuit that does the following: if the outcome of the measure is $00$, we know that no error occurred. If it's $01$ we know the first qubit was flipped, $10$ means the third qubit was fliped and, finally, $11$ means that the second qubit was flipped.

2) Now we implement the circuit on the `qasm_simulator` and see if it recognize the flips correctly.

In [ ]:
## Call the backend

backend = QasmSimulator()
shots = 2048

As a first thing, we are going to see what appens if we do nothing to it

In [ ]:
results = backend.run(qc, shots=shots).result()
answer = results.get_counts()

plt.suptitle("Syndrome measurement")
plt.bar(answer.keys(), answer.values(), color='royalblue')
plt.show()

print(answer)

Now flip each of the qubits

In [ ]:
init = QuantumRegister(3,"code")
initc = QuantumCircuit(init, QuantumRegister(2), ClassicalRegister(2))

## First qubit flipped
initc.x(init[0])
## Second qubit flipped
#initc.x(init[1])
## Third qubit flipped
#initc.x(init[2])


# Execute
results = backend.run(initc.compose(qc), shots=shots).result()
answer = results.get_counts()

plt.suptitle("Syndrome measurement for flip on single qubit")
plt.bar(answer.keys(), answer.values(), color='royalblue')
plt.show()

print(answer)


And check if our circuit recognizes correctly the bit flips.

3) Now we are going to import a noise model from a real device in order to see how effective is the QECC we created to recognize errors

In [ ]:
from qiskit.providers.fake_provider import GenericBackendV2
from qiskit_aer.noise import NoiseModel

simulator = GenericBackendV2(num_qubits=5)
noise_model = NoiseModel.from_backend(simulator)

In [ ]:
# TODO: create a circuit that initializes the circuit in |111>

init = QuantumRegister(3,"code")
initc = QuantumCircuit(init, QuantumRegister(2), ClassicalRegister(2))


# and execute the circuit with noise model


results = simulator.run(initc.compose(qc), backend=simulator, shots=shots,noise_model = noise_model).result()
answer = results.get_counts()

In [ ]:
# Print the results

plt.suptitle("Syndrome measurement with noise model")
plt.bar(answer.keys(), answer.values(), color='royalblue')
plt.show()

print(answer)

Did some error occurr during this simple initialisation?

4) Now we initialize the circuit with a generic initial state, as an example we create the state $\alpha|0\rangle+ \beta|1\rangle$ using a generic unitary on the first qubit and then we encode it in the repetition code 

In [ ]:
init = QuantumRegister(3,"code")
initc = QuantumCircuit(init, QuantumRegister(2), ClassicalRegister(2))
initc.u(0.1,0.1,0.1,init[0])  ## Use some parameters \theta, \phi, \lambda of your choice

## TO DO: write a circuit to create the repetition state on 3 qubits
initc.barrier()

generic = initc.compose(qc)

generic.draw('mpl', style={'name': 'iqx'})

In [ ]:
# Execute
results = simulator.run(generic, shots=shots,noise_model = noise_model).result()
answer = results.get_counts()

In [ ]:
# Print the results

plt.suptitle("Syndrome measurement with noise model")
plt.bar(answer.keys(), answer.values(), color='royalblue')
plt.show()

print(answer)

Did we get more or less error this time?

5) In general, gates are the source of errors during the time of our computation. Adding more gates means adding noise and therefore errors (remember the error rates indicated in the IBM Q Experience homepage). In particular, two-qubits gates are the gates with the higher error rate, this is the reason why we are going to implement an initialization circuits that ends with the preparation of |000> and contains some CNOTs in order to spot how the errors are more likely to appear in this case

In [ ]:
# Long initialization circuit to recreate |000>

init = QuantumRegister(3,"code")
initc = QuantumCircuit(init, QuantumRegister(2), ClassicalRegister(2))

## TO DO: Create a long circuit that starts with |000> and ends with |000> but
#  with arbitrary number of gates in between. See how the error increases when the depth increases

# append it at the beginning of our QECC

final = initc.compose(qc)


final.draw('mpl', style={'name': 'iqx'})

In [ ]:
# Execute
results = simulator.run(final, shots=shots,noise_model = noise_model).result()
answer = results.get_counts()

In [ ]:
# Print the results

plt.suptitle("Syndrome meaurement for a long circuit")
plt.bar(answer.keys(), answer.values(), color='royalblue')
plt.show()

print(answer)